## Welcome to your guided Notebook on building your first ML Model in Snowflake for use in Sigma

### Prerequisites

For the most part, the dual SQL and Python capabilities allows us to handle Snowflake admin tasks as needed, and you will see that this notebook creates Snowflake assets as well as executing ML code. 

However, you may need to adjust some settings on the notebook so that the code can run properly.

A. Make sure the snowflake-ml package is installed


In [ ]:
# Import required libraries and establish your Snowflake Session

# Import python packages
import streamlit as st
import pandas as pd
import snowflake.ml

# We can also use Snowpark for our analyses!
from snowflake.snowpark.context import get_active_session
session = get_active_session()


In [ ]:
-- If desired, you can establish a specific warehouse for this notebook and for use in Sigma. If you choose to do this, you will need to change the Warehouse in the "Notebook settings" using the drop down menu in the upper right section of the settings. 

-- Turn up the power! --
CREATE WAREHOUSE IF NOT EXISTS PC_SIGMA_WH;
ALTER WAREHOUSE PC_SIGMA_WH SET WAREHOUSE_SIZE = 'XSMALL';

In [ ]:
-- This cell is for people who have not yet created a connection to Snowflake within Sigma. If you already have the connection established WITH writeback, you can skip this cell. 

-- This script will:

-- 1. Uses the warehouse established in the previous cell, "PC_SIGMA_WH"
-- 2. Create a specific snowflake role that we will use in Sigma, "PC_SIGMA_ROLE"
-- 3. Grants necessary permissions to PC_SIGMA_ROLE on the database that we will be using in this analysis. "PC_SIGMA_DB"
-- 4. Creates a specific snowflake schema that we will use for writeback assets in Sigma, "PC_SIGMA_DB.WRITEBACK"
-- 5. Grants necessary permissions to PC_SIGMA_ROLE on the writeback schema
-- 6. Prints all details so that values can be copy and pasted into the Connection parameters within Sigma

SET MY_USER = CURRENT_USER();

-- Create assets for Sigma --
USE WAREHOUSE PC_SIGMA_DB;

CREATE ROLE IF NOT EXISTS PC_SIGMA_ROLE;
GRANT ALL ON DATABASE PC_SIGMA_DB TO ROLE PC_SIGMA_ROLE;
GRANT USAGE ON WAREHOUSE SIGMA_WH TO ROLE PC_SIGMA_ROLE;

GRANT ROLE PC_SIGMA_ROLE TO ROLE SYSADMIN;
GRANT ROLE PC_SIGMA_ROLE TO USER IDENTIFIER($MY_USER);

 -- Create writeback --
CREATE SCHEMA IF NOT EXISTS PC_SIGMA_DB.WRITEBACK;

GRANT ALL ON DATABASE PC_SIGMA_DB TO ROLE PC_SIGMA_ROLE;
GRANT ALL ON SCHEMA PC_SIGMA_DB.WRITEBACK TO ROLE PC_SIGMA_ROLE;

SELECT CURRENT_ACCOUNT(), CURRENT_WAREHOUSE(), CURRENT_USER(), '**PASSWORD**', 'PC_SIGMA_ROLE', 'PC_SIGMA_DB' as Writeback_DB, 'WRITEBACK' as Writeback_Schema;

-- May need to use the account name with the Cloud location - bottom left icon


In [ ]:
# This establishes the Database, Writeback Schema, and Role that we will use for the rest of the script. 
# As a default, this uses the names from the above cell. If you have different credentials, please replace these variables. 

Database = "PC_SIGMA_DB"
Writeback_Schema = "WRITEBACK"
Role = "PC_SIGMA_ROLE"


In [ ]:
from snowflake.ml.registry import Registry

session.sql(f"CREATE SCHEMA IF NOT EXISTS {Database}.ML_REGISTRY").collect()
session.sql(f"GRANT USAGE ON SCHEMA ML_REGISTRY TO ROLE {Role}").collect()

reg = Registry(session, database_name=Database, schema_name="ML_REGISTRY")

### Run your Sigma Analysis!

Link to download the CSV file containing Seattle shift sales ( [Download Here](https://sigma-quickstarts-main.s3.us-west-1.amazonaws.com) )

In [ ]:
# Specify inputs
training_table = session.table(f"{Database}.{Writeback_Schema}.TRAIN_HOL")
testing_table = session.table(f"{Database}.{Writeback_Schema}.TEST_HOL")

# Calculate total shift sales by location_id
training_table_df = training_table.to_pandas()

# Run
training_table_df.groupby("LOCATION_ID")["SHIFT_SALES"].sum().reset_index()


In [ ]:
# Input my analyst's ideas for features
feature_cols = [
    "MONTH_OF_DATE",
    "WEEKDAY_OF_DATE",
    "ENCODED_SHIFT"
]
target_col = "SHIFT_SALES"

In [ ]:
from snowflake.ml.modeling.tree import DecisionTreeRegressor
# More models shown here: https://docs.snowflake.com/en/developer-guide/snowpark-ml/reference/latest/modeling

my_model = DecisionTreeRegressor()
my_model.set_input_cols(feature_cols)
my_model.set_label_cols(target_col)
my_model.set_output_cols("PRED_" + target_col)

my_model.fit(training_table)

In [ ]:
# Using the `metrics` module to calculate mean absolute error, which is pretty explanatory:
# "how many dollars off, on average, is each prediction?"

from snowflake.ml.modeling.metrics import mean_absolute_error

predictions = my_model.predict(testing_table)
mae_score = mean_absolute_error(
    df=predictions, y_true_col_names="SHIFT_SALES", y_pred_col_names="PRED_SHIFT_SALES"
)
mae_score

In [ ]:
# Log the model
model_ver = reg.log_model(
    model_name="SHIFT_SALES_MODEL", version_name="Version_1", model=my_model
)

# Add a description to the model -
model_ver.set_metric(metric_name="MAE Score", value=mae_score)
model_ver.comment = "This DecisionTreeRegressor model predicts the Shift Sales for a given Location, using Features discovered through Sigma"

reg.get_model("SHIFT_SALES_MODEL").show_versions()

In [ ]:
session.sql(f"GRANT USAGE ON SCHEMA {Database}.ML_REGISTRY TO ROLE {Role};").collect()
session.sql(f"GRANT USAGE ON ALL MODELS IN SCHEMA {Database}.ML_REGISTRY TO ROLE {Role};").collect()

In [ ]:
inf_model = reg.get_model("SHIFT_SALES_MODEL")
inf_model.default = "Version_1"
inf_model.default.fully_qualified_model_name + "!Predict, " + ", ".join(feature_cols)

In [ ]:
session.sql(f"SELECT {Database}.ML_REGISTRY.SHIFT_SALES_MODEL!Predict(1, 2, 1)")